# Description

This notebook provides a first look at the FC matrices that form this data sample:

* Load all connectivity matrices

* Compute the average connectivity matrix across the whole sample

* Plot the average FC for the whole sample

* Create dashboard to fastly explore all the individual scan FC matrices

In [1]:
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)

In [2]:
import pandas as pd
import xarray as xr
import numpy as np
import os.path as osp
import hvplot.pandas
from tqdm import tqdm
import matplotlib.pyplot as plt
#import holoviews as hv
from utils.basics import get_sbj_scan_list
from scipy.spatial.distance import squareform
from utils.basics import DATA_DIR, CORTICAL_400ROI_ATLAS_NAME, FB_400ROI_ATLAS_NAME, ATLASES_DIR, FB_200ROI_ATLAS_NAME
from utils.plotting import hvplot_fc, plot_fc
from sfim_lib.io.afni import load_netcc
from scipy.spatial.distance import cosine      as cosine_distance
from scipy.spatial.distance import correlation as correlation_distance
from scipy.spatial.distance import euclidean   as euclidean_distance
import seaborn as sns
import panel as pn
from sklearn.utils.validation import check_symmetric

/data/SFIMJGC_HCP7T/Apps/envs/fc_introspection_2023b_py310/lib/python3.10/site-packages/nxviz/__init__.py:18: UserWarning: 
nxviz has a new API! Version 0.7.4 onwards, the old class-based API is being
deprecated in favour of a new API focused on advancing a grammar of network
graphics. If your plotting code depends on the old API, please consider
pinning nxviz at version 0.7.4, as the new API will break your old code.

To check out the new API, please head over to the docs at
https://ericmjl.github.io/nxviz/ to learn more. We hope you enjoy using it!

(This deprecation message will go away in version 1.0.)

  warnings.warn(


In [3]:
import os
port_tunnel = int(os.environ['PORT2'])
print('++ INFO: Second Port available: %d' % port_tunnel)

++ INFO: Second Port available: 39317


In [4]:
ATLAS_NAME = FB_400ROI_ATLAS_NAME

# 1. Load the final list of scans used in this project

In [5]:
sbj_list, scan_list = get_sbj_scan_list(when='post_motion', return_snycq=False)

++ [post_motion] Number of subjects: 133 subjects
++ [post_motion] Number of scans:    471 scans


# 2. Load information about the Atlas and ROI needed for plotting

In [6]:
ATLASINFO_PATH = osp.join(ATLASES_DIR,ATLAS_NAME,f'{ATLAS_NAME}.roi_info.csv')
roi_info       = pd.read_csv(ATLASINFO_PATH)
roi_info

ROI_ID Hemisphere      Network                 ROI_Name  pos_R  pos_A  \
0         1         LH          Vis                 LH_Vis_1    -32    -42   
1         2         LH          Vis                 LH_Vis_2    -30    -32   
2         3         LH          Vis                 LH_Vis_3    -36    -62   
3         4         LH          Vis                 LH_Vis_4    -24    -54   
4         5         LH          Vis                 LH_Vis_5    -24    -72   
..      ...        ...          ...                      ...    ...    ...   
375     376         RH      Default     RH_Default_pCunPCC_9      8    -50   
376     377         RH  Subcortical   RH_Subcortical_Caudate     14     13   
377     378         RH  Subcortical   RH_Subcortical_Putamen     26      4   
378     379         RH  Subcortical  RH_Subcortical_Pallidum     22      0   
379     380         RH  Subcortical  RH_Subcortical_Thalamus     12    -18   

     pos_S  color_R  color_G  color_B      RGB  
0      -20      120       17      128  #781180  
1      -18      120       17      129  #781181  
2      -16      120       17      130  #781182  
3       -8      120       17      131  #781183  
4      -10      120       17      132  #781184  
..     ...      ...      ...      ...      ...  
375     44      208       64       77  #d0404d  
376     -7      255      255        0  #ffff00  
377     -1      255      255        0  #ffff00  
378      0      255      255        0  #ffff00  
379     -6      255      255        0  #ffff00  

[380 rows x 11 columns]

# 3. Load into memory all individual scan FC matrices

We will place the matrices in two separate xr.DataArray data structures. One will hold the matrices in terms of Pearson's correlation (```all_sfc_R```) and the other one in terms of their Fisher's transform (```all_sfc_Z```). In the first cell below, we create empty versions of these two data structures. These empty data structures will get populated in the subsequent cell.

In [7]:
unique_sbj_ids = list(pd.Series([sbj for sbj,_ in scan_list]).unique())
unique_run_ids = list(pd.Series([run for _,run in scan_list]).unique())

In [8]:
# Create empty Xr Data Array to hold all FC matrices
all_sfc_R = xr.DataArray(dims=['Subject','Run','ROI1','ROI2'], 
                         coords={'Subject':unique_sbj_ids,
                                 'Run': unique_run_ids,
                                 'ROI1':roi_info['ROI_Name'].values,
                                 'ROI2':roi_info['ROI_Name'].values})
all_sfc_Z = xr.DataArray(dims=['Subject','Run','ROI1','ROI2'], 
                         coords={'Subject':unique_sbj_ids,
                                 'Run': unique_run_ids,
                                 'ROI1':roi_info['ROI_Name'].values,
                                 'ROI2':roi_info['ROI_Name'].values})

In [9]:
%%time
all_rois = list(roi_info['ROI_Name'].values)
# Load all matrices
for sbj,run in tqdm(scan_list):
    _,_,_,_,run_num,_,run_acq = run.split('-')
    netcc_path = osp.join(DATA_DIR,'PrcsData',sbj,'preprocessed','func','pb06_staticFC',f'{run_acq}_run-{run_num}.{ATLAS_NAME}_000.netcc')
    netcc      = load_netcc(netcc_path)
    this_scan_rois = [ item.strip().strip('7Networks_') for item in list(netcc.columns)]
    all_sfc_R.loc[sbj,run,:,:] = netcc
    all_sfc_Z.loc[sbj,run,:,:] = netcc.apply(np.arctanh)

100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 471/471 [00:11<00:00, 42.46it/s]

CPU times: user 9.47 s, sys: 1.52 s, total: 11 s
Wall time: 11.1 s


# 4. Compute the average matrix for the whole sample

To compute the sample mean, we first Fisher's transform each individual matrix, average those, and do the inverse transform of the average

In [10]:
REFERENCE_fc = np.tanh(all_sfc_Z.mean(dim=['Subject','Run'])).values

Put the matrix into a properly annotated DataFrame structure

In [11]:
REFERENCE_fc = pd.DataFrame(REFERENCE_fc, columns=list(roi_info['ROI_Name']),index=list(roi_info['ROI_Name']))
REFERENCE_fc.index.name   = 'ROI1'
REFERENCE_fc.columns.name = 'ROI2'

Plot the sample mean (or Reference) FC matrix

In [13]:
hvplot_fc(REFERENCE_fc, ATLASINFO_PATH, cbar_title='Average FC for the whole sample', cmap='RdBu_r', major_label_overrides = 'regular_grid')

:Overlay
   .HeatMap.I   :HeatMap   [columns,index]   (value)
   .HLine.I     :HLine   [x,y]
   .VLine.I     :VLine   [x,y]
   .HLine.II    :HLine   [x,y]
   .VLine.II    :VLine   [x,y]
   .HLine.III   :HLine   [x,y]
   .VLine.III   :VLine   [x,y]
   .HLine.IV    :HLine   [x,y]
   .VLine.IV    :VLine   [x,y]
   .HLine.V     :HLine   [x,y]
   .VLine.V     :VLine   [x,y]
   .HLine.VI    :HLine   [x,y]
   .VLine.VI    :VLine   [x,y]
   .HLine.VII   :HLine   [x,y]
   .VLine.VII   :VLine   [x,y]
   .HLine.VIII  :HLine   [x,y]
   .VLine.VIII  :VLine   [x,y]
   .HLine.IX    :HLine   [x,y]
   .VLine.IX    :VLine   [x,y]
   .HLine.X     :HLine   [x,y]
   .VLine.X     :VLine   [x,y]
   .HLine.XI    :HLine   [x,y]
   .VLine.XI    :VLine   [x,y]
   .HLine.XII   :HLine   [x,y]
   .VLine.XII   :VLine   [x,y]
   .HLine.XIII  :HLine   [x,y]
   .VLine.XIII  :VLine   [x,y]
   .HLine.XIV   :HLine   [x,y]
   .VLine.XIV   :VLine   [x,y]
   .HLine.XV    :HLine   [x,y]
   .VLine.XV    :VLine   [x,y]
   .HLine.XVI   :HLine   [x,y]
   .VLine.XVI   :VLine   [x,y]
   .HLine.XVII  :HLine   [x,y]
   .VLine.XVII  :VLine   [x,y]
   .HLine.XVIII :HLine   [x,y]
   .VLine.XVIII :VLine   [x,y]
   .HLine.XIX   :HLine   [x,y]
   .VLine.XIX   :VLine   [x,y]
   .Segments.I  :Segments   [x0,y0,x1,y1]   (Networks)
   .Segments.II :Segments   [x0,y0,x1,y1]   (Hemispheres)

# 5. Explore individual subject matrices

In [14]:
sbj_level_sfc_R = np.arctan(all_sfc_Z.mean(dim='Run'))

In [15]:
sbj_select = pn.widgets.Select(name='Subject', options=unique_sbj_ids)
@pn.depends(sbj_select)
def plot_subject_fc(sbj):
    this_subject_mat = pd.DataFrame(sbj_level_sfc_R.loc[sbj].values, index=list(sbj_level_sfc_R.coords['ROI1'].values), columns=list(sbj_level_sfc_R.coords['ROI2'].values))
    return hvplot_fc(this_subject_mat, ATLASINFO_PATH, cbar_title='FC '+sbj, cmap='RdBu_r', major_label_overrides = 'regular_grid')
sbj_mat_dashboard = pn.Row(sbj_select, plot_subject_fc)

In [16]:
sbj_mat_dashboard_server = sbj_mat_dashboard.show(port=port_tunnel,open=False)

Launching server at http://localhost:39317


In [17]:
sbj_mat_dashboard_server.stop()